# Seminar Problemorientierte Programmierung

## 9 Fallstudie: Wortspiele
[Chapter 9: Case study: Word play](http://greenteapress.com/thinkpython2/html/thinkpython2010.html)

In diesem Abschnitt gibt es die zweite Fallstudie. In dieser werden Wort-Rätsel gelöst, in denen Wörter mit bestimmten Eigenschaften gesucht werden. Beispielsweise finden wir die längsten Palindrome und suchen nach Wörtern, deren Buchstaben in alphabetischer Reihenfolge erscheinen. Und wir lernen eine weitere Entwicklungsmethode kennen: Rückführung auf ein bereits gelöstes Problem.

### Ihre Lernziele:

Beschreiben Sie in 2-3 Stichpunkten kurz was Sie im Seminar heute lernen wollen. Klicken Sie dazu doppelt auf diesen Text und bearbeiten Sie dann den Text:

- 
- 
- 

## Exkurs: Was mir an Python gefällt

Dieser Code enthält das Grundgerüst, um eine auf TCP basierende Serveranwendung zu programmieren.

In [ ]:
# Quellen: https://docs.python.org/3/howto/sockets.html und 
# http://www.binarytides.com/python-socket-server-code-example/

import socket

# function for handling connections. This will be used to create threads
def client_thread(conn):
    # sending message to connected client
    conn.send(bytearray('Welcome to the server. Type something and hit enter\n', "utf-8")) #send only takes string
     
    # infinite loop so that function do not terminate and thread do not end.
    while True:
         
        # receiving from client
        data = conn.recv(1024)
        if not data: 
            break
        # print on server side
        print(data.decode("utf-8"))
        # echo to client side
        reply = bytearray('OK ... ', "utf-8") + data
        conn.sendall(reply)
     
    # came out of loop
    conn.close()
    
# create an INET, STREAMing socket
serversocket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
# bind the socket to a public host, and a port
# serversocket.bind((socket.gethostname(), 8080))
# use localhost instead 
serversocket.bind(("localhost", 8080))
# become a server socket
serversocket.listen(5)


while True:
    # accept connections from outside
    (clientsocket, address) = serversocket.accept()
    # now do something with the clientsocket
    # in this case, we'll pretend this is a threaded server
    ct = client_thread(clientsocket)
    ct.run()

serversocket.close()

Wenn Sie den Code starten und sich dann mit Hilfe von Telnet mit der Anwendung verbinden (telnet localhost 8080), werden alle Eingaben an Sie zurückgespiegelt ("echo") und hier in Jupyter ausgegeben. Das ist eine sehr einfache Testanwendung, die aus Sicherheitsgründen nur von Ihrem Rechner aus erreichbar ist.

Falls Ihr Rechner keinen Paketfilter ("Firewall") laufen hat und Sie die Zeile mit localhost auskommentieren und stattdessen die mit socket.gethostbyname() aktivieren, dann ist die Anwendung ggf. auch von anderen Rechnern erreichbar und stellt ziemlich sicher eine Sicherheitslücke dar. Gehen Sie also vorsichtig mit dieser Option um.



### 9.1 Wortlisten einlesen

Die Übungen in diesem Abschnitt weichen vom [Original](http://greenteapress.com/thinkpython2/html/thinkpython2010.html) insofern ab, als dass Wortlisten mit deutschen Wörtern verwendet werden. Alle Übungen können jedoch auch mit englischen Wortlisten durchgeführt werden.

Für die Übungen in diesem Abschnitt benötigen wir eine Liste deutscher Wörter. Es gibt sehr viele Wortlisten im Web, wir verwenden hier eine Liste des [Wortschatz-Projektes](http://wortschatz.uni-leipzig.de/) der Universität Leipzig. Laden Sie [diese Liste mit 10000 häufigen deutschen Wörtern](http://pcai056.informatik.uni-leipzig.de/downloads/etc/legacy/Papers/top10000de.txt) herunter und speichern Sie sie unter dem Dateinamen `top10000de.txt`.

Die Datei ist eine reine Textdatei, daher können wir sie mit einem Texteditor anschauen. Wir können sie aber auch leicht mit Python einlesen. Die eingebaute Funktion `open` erwartet einen Dateiname als Parameter und gibt uns ein **Dateiobjekt** (*file object*) zurück, mit dessen Hilfe wir die Datei lesen können:

In [ ]:
fin = open('top10000de.txt', encoding="latin1")
# Hinweis: der Parameter encoding gibt an, in welcher Zeichenkodierung
# die Datei verfasst ist. Im Allgemeinen sollten Dateien heute in Unicode codiert
# sein, bei diesen ist in Python3 diese Angabe nicht notwendig.
# Leider ist die Datei vom Wortschatz-Projekt aber noch in der
# Latin1-Kodierung, so dass wir dies Python mitteilen müssen.

`fin` ist ein üblicher Name für ein Dateiobjekt zum lesenden Zugriff auf die Datei (`fin` steht für **f**ile **in**put). Das Dateiobjekt bietet uns mehrere Methoden zum Lesen der Datei, unter anderem die Methode `readline`, die Zeichen aus einer Datei einliest, bis ein Zeichen für den Zeilenumbruch erreicht wird, und das Ergebnis als Zeichenkette zurückgibt:

In [ ]:
fin.readline()

Das erste "Wort" in dieser Liste ist "der". Die Zeichenfolge "\n" repräsentiert das Zeichen für den Zeilenumbruch, durch das die Wörter (zeilenweise) getrennt sind. 

Das Dateiobjekt merkt sich, an welcher Stelle innerhalb der Datei wir gerade sind. Wenn wir also `readline` nochmal aufrufen, erhalten wir die nächste Zeile zurück:

In [ ]:
fin.readline()

Das nächste Wort ist also "die". Wenn uns das Zeichen für den Zeilenumbruch stört, können wir es mit der Methode `strip` entfernen: 

In [ ]:
line = fin.readline()
word = line.strip()
word

Wir können das Dateiobjekt auch innerhalb einer `for`-Schleife verwenden. Das folgende Programm liest die Datei ein und gibt jedes Wort aus – eines pro Zeile:

In [ ]:
fin = open('top10000de.txt', encoding="latin1")
for line in fin:
    word = line.strip()
    print(word)

Diese Schleife können Sie leicht nutzen, um nach Wörtern mit bestimmten Eigenschaften zu suchen. Gibt es im Deutschen Wörter, die auf "gry" enden? Oder zumindest auf "ry"?

<details>
    <summary type="button" class="btn btn-info">Hinweis</summary>
  <div class="alert alert-info" role="alert">

Mit der Zeichenkettenfunktion [endswith](https://docs.python.org/3/library/stdtypes.html#str.endswith) können Sie prüfen, ob eine Zeichenkette auf eine andere Zeichenkette endet. Zusammen mit einer Verzweigung (`if`) können Sie damit nur die entsprechenden Wörter ausgeben.
      
  </div>       
</details>  
  

![The fifth panel also applies to postmodernists](https://imgs.xkcd.com/comics/words_that_end_in_gry.png)

[Words that end in GRY](https://xkcd.com/169/), Randall Munroe

### 9.2 Übung

Die Lösungen der Aufgaben gibt es wie gehabt unter der jeweiligen Aufgabe und mit ergänzender Theorie im nächsten Abschnitt. Bitte versuchen Sie zunächst, jede Aufgabe selbständig zu lösen, bevor sie eine der Lösungen anschauen.

#### Aufgabe 1

Schreiben Sie ein Programm welches die Datei `top10000de.txt` einliest und nur die Wörter mit mehr als 20 Zeichen ausgibt.

In [ ]:
# Implementieren Sie hier Ihr Programm


Am Ergebnis werden Sie merken, dass die Wortliste nicht ganz bereinigt ist und manche Zeilen Phrasen bestehend aus mehreren Wörtern enthalten.  

![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Öffnen Sie die Datei in einer neuen Variablen und rufen Sie diese im Funktionskopf auf.
2. Um zu überprüfen, ob ein Wort lang genug ist, müssen Sie jede Zeile einzeln aufrufen. Verwenden Sie dafür eine `for`- Schleife, die Sie zuvor gesehen haben.
3. Für jede Zeile müssen Sie nun prüfen ob die Bedungung erfüllt ist. Wie könnte diese Bedingung aussehen?
4. Wenn die Bedinung erfüllt ist, geben Sie die entsprechende Zeile mit einem `print`-Statement aus. Verwenden Sie nicht `return`, da Sie die Funktion so sofort beenden und nur das erste Element finden würden, dass die Bedingung erfüllt.
5. Schreiben Sie den Funktionsaufruf und schauen Sie sich das Ergebnis an.

In [ ]:
fin = open('top10000de.txt', encoding="latin1")

def long(fin):
    """Findet Zeilen mit mehr als 20 Buchstaben aus einer beliebigen Wortliste im txt Format"""
    for line in fin:
        if len(line)>20:
            print (line.strip())
            
            
long(fin)


#### Aufgabe 2

![Ernest Vincent Wright](https://upload.wikimedia.org/wikipedia/commons/thumb/a/af/Ernestvincentwright1939.jpg/371px-Ernestvincentwright1939.jpg)

1939 hat [Ernest Vincent Wright](https://de.wikipedia.org/wiki/Ernest_Vincent_Wright) den englischen Roman *Gadsby* mit 50000 Wörtern veröffentlicht, von denen keines den Buchstaben "e" enthält. Da "e" der häufigste Buchstabe im Englischen ist, ist das eine beachtliche Leistung.

Tatsächlich ist's knifflig, was im Hirn ohn' das Symbol zu tun. (Im Englischen ist es wohl einfacher - im Original steht hier: *In fact, it is difficult to construct a solitary thought without using that most common symbol. It is slow going at first, but with caution and hours of training you can gradually gain facility. All right, I’ll stop now.*)

Schreiben Sie eine Funktion `has_no_e` die `True` zurückgibt, wenn das übergebene Wort den Buchstaben "e" nicht enthält. (Denken Sie auch an den Großbuchstaben "E".)

In [ ]:
def has_no_e(word):
    # Implementieren Sie hier die Funktion has_no_e


![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Schreiben Sie den Funktionskopf und legen Sie fest welche Rückgabewerte es gibt. (Wenn kein `e` vorkommt, `True`, sonst `False`.)
2. Um jeden Buchstaben in dem Wort zu prüfen, schreiben Sie eine `for`-Schleife, wie in [Abschnitt 8.3](seminar08.ipynb#Durchlauf-mit-einer-for-Schleife) gezeigt.
3. Prüfen Sie für jeden Buchstaben, ob er `e` ist. Denken Sie dabei daran, dass die Buchstaben sowohl groß als auch klein geschrieben sein können. Wenn der Buchhstabe `e` ist, kann der Test sofort abgebrochen und die Schleife mit `return False` verlassen werden.
4. Wenn in der Schleife nie eine `return`-Anweißung erreicht wird, wird die Schleife verlassen und `True` zurückgegeben.

In [ ]:
def has_no_e(word):
    for letter in word: 
        if letter == 'e':
            return False
        if letter == 'E':
            return False
    return True
        
has_no_e('nicht')

Verändern Sie jetzt das Programm aus Aufgabe 1 so, dass nur Wörter ausgegeben werden, die kein "e" enthalten und berechnen Sie den Anteil der Wörter in der Liste, die kein "e" enthalten.

In [ ]:
# Implementieren Sie hier Ihr Programm



![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Gehen Sie hier analog zu Aufgabe 1 vor, kopieren Sie ruhig den Code, den Sie für Aufgabe 1 geschrieben haben, so verringern Sie die Gefahr von Tippfehlern.
2. Verändern Sie die `if`-Verzweigung so, dass Sie `has_no_e` aufruft und den Rückgabewert prüft. Liefert `has_no_e` `True` zurück wird das Wort ausgegeben.
3. Um den Anteil zu bestimmen, müssen wir zählen auf wie viele Worte die Bedingung zutrifft. Legen Sie dafür eine Variable an und initialisieren Sie sie mit 0.
4. Immer wenn Sie das Wort ausgeben inkrementieren Sie den Zähler.
5. Um den Anteil zu berechnen teilen Sie diese Variable durch die Gesamtmenge an Wörtern, in diesem Fall 10000. Vergessen Sie nicht die so berechnete Zahl auszugeben.

In [ ]:
fin = open('top10000de.txt', encoding="latin1")
def test(fin):
    count=0
    for line in fin:
        if has_no_e(line):
            count=count+1
            print(line)
    anteil=count/10000
    print(anteil)
            
test(fin)

#### Aufgabe 3

Schreiben Sie eine Funktion `avoids` die ein Wort sowie eine Zeichenkette mit verbotenen Buchstaben erwartet und `True` zurückgibt, wenn im Wort keiner der verbotenen Buchstaben auftaucht. 

*Hinweis: mit der Methode `lower` können Sie eine Zeichenkette in Kleinbuchstaben umwandeln. `word.lower()` enthält also die gleichen Buchstaben wie `word`, nur halt als Kleinbuchstaben*


In [ ]:
def avoids(word, forbidden):
    # Implementieren Sie hier die Funktion


![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)


1. Diese Aufgabe ist eine Verallgemeinerung von `has_no_e`.
2. Auch in dieser Aufgabe muss das Wort Buchstabe für Buchstabe überprüft werden.
3. Der Vergleich findet allerdings nicht mit `e` statt, sondern mit dem zusätzlich eingegebenen Buchstaben.
4. Da wir im Vorfeld nicht wissen, um welchen Buchstaben es sich handelt, können wir nicht einfach zwei Tests durchführen, sondern müssen stattdessen das Wort vereinheitlichen. Nutzen Sie dazu `word.lower()`.

In [ ]:
def avoids(word, forbidden):
    for letter in word.lower():
        if letter in forbidden:
            return False
    return True


avoids("ad", "f,g,h")



Verändern Sie Ihr Programm von Aufgabe 2, so dass Sie zunächst die Nutzer bitten, die verbotenen Buchstaben einzugeben und dann drucken Sie die Anzahl der Wörter aus, die keine der Buchstaben enthalten.

In [ ]:
# Implementieren Sie hier Ihr Programm

Können Sie eine Kombination von fünf verbotenen Buchstaben finden, die die kleinste Anzahl an Wörtern ausschließt? (*Bestwert unter den 10000 Wörtern der Liste ist bisher 590.*)


![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Auch dieser Test funktioniert analog zum ersten Test. Kopieren Sie die Funktion, geben Sie ihr einen neuen Namen und passen Sie sie an. Dadurch vermeiden Sie eventuelle Flüchtigkeitsfehler.
2. Aus der Aufgabenstellung geht hervor, dass wir eine Nutzereingabe brauchen. Verwenden Sie dafür `input`. 
3. Stellen Sie sicher, dass die Eingabe aus `input` einer Variablen zugewießen wird.
4. Rufen Sie dann in der Schleife `avoids` mit dem User-Input auf. Um zu sehen, wie viele Worte Sie nicht ausgeschlossen haben, verwenden Sie den Zähler.
5. Geben Sie diesen Zähler nach Verlassen der `for`-Schleife einmalig aus.

In [ ]:
fin = open('top10000de.txt', encoding="latin1")

def test2(fin):
    forbidden=input("Geben Sie Buchstaben ein, die nicht vorkommen sollen:\n")
    count=0
    print("Dies sind die übrigen Worte:")
    for line in fin:    
        word=line.strip()
        if avoids(word, forbidden):
            count=count+1
            print (word)
    print (count)
test2(fin)

#### Aufgabe 4

Schreiben Sie eine Funktion `uses_only` die ein Wort und eine Zeichenkette mit Buchstaben als Argument erwartet und `True` zurückgibt, wenn das Wort nur Buchstaben aus der Liste enthält. 

In [ ]:
def uses_only(word, characters):
    # Implementieren Sie hier die Funktion


![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Auch hier können Sie Code wiederverwenden. Überlegen Sie wie Sie den Code anpassen können.
2. Diesmal wollen Sie nicht prüfen, ob der Buchstabe verboten ist. Stattdessen interessiert uns, ob er erlaubt ist.
3. Sie müssen die Prüfung also negativ, nicht positiv formulieren. Wenn ein Buchstabe des Wortes nicht in der verfügbaren Liste zu finden ist, kann das Programm abbrechen und `False` zurück geben.


In [ ]:
def uses_only(word, available):
    for letter in word.lower(): 
        if letter not in available:
            return False
    return True

uses_only("acefhln", "acefhln")

Können Sie einen Satz bilden, der nur die Buchstaben `acefhln` enthält? Nutzen Sie ihr Programm um alle Worte auf der Liste zu finden, die Sie verwenden dürfen.

In [ ]:
# Implementieren Sie hier Ihr Programm

![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Wie gehabt, können Sie Code wiederverwenden und es ist empfehlenswert, das zu tun, da Sie so viele Flüchtigkeitsfehler vermeiden können. Nehmen Sie am besten den Testcode, den Sie für `forbidden` verwendet haben.
2. Sie müssen den Testcode natürlich anpassen. Als erstes können Sie die `if`-Verzweigung verändern. Welche Funktion wird aufgerufen, um zu testen, ob ein Wort die Bedingung erfüllt?
3. Wenn Sie dies angepasst haben, schauen Sie, was Sie an die Funktion übergeben müssen. Das Wort wird automatisch in der Schleife übergeben, aber die Liste der verfügbaren Buchstaben müssen Sie manuell anpassen. Da eine Nutzereingabe nicht notwendig ist, können Sie der Variablen einfach einen String zuweißen, der alle erlaubten Buchstaben enthält.
4. Drucken Sie alle Worte aus, die die Bedingung erfüllen, und versuchen Sie aus den Worten einen Satz zu bilden.
*Hinweiß: Ich habe mich entschieden die Zählervariable zu behalten, da Sie mir sagt, wie viele Worte ich zur Verfügung habe. Dies ist nicht notwendig.*

In [ ]:


fin = open('top10000de.txt', encoding="latin1")

    
    
def sentence(fin):
    available="acefhln"
    count=0
    for line in fin:
        word=line.strip()
        if uses_only(word, available):
            count=count+1
            print(line)
    return count
    

sentence(fin)

#Elf Fahnen lehnen an Helene
#Aber ich bin sicher Sie können einen besseren Satz bilden. Viel Erfolg!

#### Aufgabe 5
Schreiben Sie eine Funktion `uses_all` die ein Wort und eine Zeichenketten mit verlangten Buchstaben erwartet und `True` zurückgibt, wenn das Wort alle verlangten Buchstaben mindestens einmal enthält. 

In [ ]:
def uses_all(word, characters):
    # Implementieren Sie hier die Funktion



![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Wenn Sie das Wort Buchstabe für Buchstabe durchgehen, können Sie sicherstellen, dass nur erlaubte Buchstaben verwendet werden. Können Sie so auch sicherstellen, dass alle Buchstaben verwendet werden? Probieren Sie es aus.
2. Da es so nicht möglich ist, überlegen Sie, wie Sie sicherstellen können, dass alle Buchstaben verwendet werden. Sie können dafür die Strukturen verwenden, die Sie bereits kennen. 
3. Wir haben gesehen, dass wir unseren Buchstaben mit einer ganzen Liste an Buchstaben vergleichen können. In diesem Fall behandeln wir word.lower() als diese Liste und die Liste mit vorgegebenen Buchstaben als unser Wort. Gehen Sie die Liste also Buchstabe für Buchstabe durch und gleichen Sie Sie mit word.lower() ab. Überprüfen Sie wann `True` und wann `False` zurückgegeben wird.

In [ ]:
def uses_all(word, required):
    for letter in required: 
        if letter not in word.lower():
            return False
    return True
uses_all("Hallo", "ahlo")

Wie viele Wörter gibt es, in denen die Vokale `aeiou` alle vorkommen?

In [ ]:
# Implementieren Sie hier Ihr Programm


In der Ergebnisliste sollte das Wort `Argumentation` enthalten sein.


![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Wie gehabt können Sie den Test kopieren. Bennenen Sie ihn um und passen Sie auf, dass Sie den Namen auch in dem Funktionsaufruf ändern. 
2. Hier wird gefragt, wie viele Wörter alle Vokale enthalten, der Zähler ist also ein notwendiges Element der Funktion. 
3. Wie müssen sie die `if`-Anweißung anpassen, was ist die zweite Variable, die Sie der Funktion übergeben?

In [ ]:
def all_vowels(fin):
    required='aeiou'
    count=0
    for line in fin:
        word=line.strip()
        if uses_all(word, required):
            count=count+1
            print(line)
    return count



fin = open('top10000de.txt', encoding="latin1")
all_vowels(fin)

#### Aufgabe 6

Schreiben Sie eine Funktion `is_abecedarian` die `True` zurückgibt, wenn die Buchstaben in einem Wort in alphabetischer Reihenfolge auftauchen (doppelte Buchstaben sind erlaubt). 

In [ ]:
def is_abecedarian(word):
    # Implementieren Sie hier die Funktion



![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Hier gibt es verschiedene richtige Lösungen. Weiter unten werden 3 verschiedene Lösungen vorgestellt und es kann sein, dass sich Ihr Ansatzt von dem hier präsentierten unterscheiden. Das heißt nicht zwingend, dass Ihr Ansatz falsch ist. Schauen Sie sich gegebenenfalls die Lösung weiter unten an, wenn Sie sich unsicher sind.
2. Der hier verwendete Ansatz verwendet eine `for`-Schleife.  
3. Es wird eine Hilfsvariable benötigt, die den letzten Buchstaben speichert, damit die Buchstaben miteinander verglichen werden können. Diese wird vor der Schleife auf den ersten Buchstaben des Wortes gesetzt. 
4. in jedem Durchlauf der Schleife wird der aktuelle Buchstabe mit dem vorherigen verglichen. Wenn er kleiner ist, wird `False` zurückgegeben, sonst wird `previous` auf `letter` gesetzt. 
5. Wird die Schleife verlassen, ohne das `False` zurückgegeben wurde, wird `True` zurückgegeben. 

In [ ]:
def is_abecedarian(word):
    previous=word[0]
    for letter in word.lower():
        if letter<previous:
            return False
        previous=letter
    return True

is_abecedarian("beginnt")

Wie viele solcher Wörter können Sie in der Liste finden?

In [ ]:
# Implementieren Sie hier Ihr Programm

*(Das längste Wort mit dieser Eigenschaft in der Liste ist `beginnt`.)*

![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Wie gehabt ist dies eine Abwandlung des ersten Tests, den Sie geschrieben haben. Kopieren Sie also eine der Testanweißungen. Da nach der Anzahl der Worte mit dieser Eigenschaft gefragt ist, bietet es sich an, einen der Tests zu kopieren, der bereits count enthält. 
2. Überlegen Sie, wie Sie diese Funktion anpassen müssen. An welcher Stelle wird `is_abecedarian()` aufgerufen, was passiert wenn `is_abecedarian() True` zurückgibt?
3. Vergessen Sie nicht die .txt datei zu öffnen und zu übergeben. 

In [ ]:
def abecedarian(fin):
    count=0
    for line in fin:
        word=line.strip()
        if is_abecedarian(word):
            count=count+1
            print(line)
    return count




fin = open('top10000de.txt', encoding="latin1")
abecedarian(fin)

![State Word Map](https://imgs.xkcd.com/comics/state_word_map.png)

[State Word Map](https://xkcd.com/1845/), Randall Munroe

Die Wortliste erlaubt uns viele interessante Fragestellungen zu beantworten. Welches ist beispielsweise das längste Wort in der Wortliste? [Wikipedia zu den längsten Wörtern im Deutschen](https://en.wikipedia.org/wiki/Longest_words#German)

### 9.3 Suche

Alle Beispiele im vorherigen Abschnitt haben eines gemeinsam: sie können mit dem Suchmuster gelöst werden, welches wir in [Abschnitt 8.6](seminar08.ipynb#8.6-Suche) kennengelernt haben. Das einfachste Beispiel ist:

In [ ]:
def has_no_e(word):
    for letter in word.lower():
        if letter == 'e':
            return False
    return True

Die `for`-Schleife geht über die Zeichen in `word` (genau genommen nach der Umwandlung in Kleinbuchstaben, wegen der Verwendung von `lower`). Falls wir den Buchstaben "e" finden, können wir sofort `False` zurückgeben; ansonsten gehen wir zum nächsten Buchstaben. Wenn wir die Schleife ganz normal verlassen, d.h. wenn wir kein "e" gefunden haben, geben wir `True` zurück.

Wir können diese Funktion noch etwas kompakter schreiben, indem wir den `in`-Operator verwenden, aber ich habe Ihnen diese Variante präsentiert, weil sie die Logik hinter der Suche demonstriert.

`avoids` ist eine verallgemeinerte Version von `has_no_e` aber sie hat die gleiche Struktur:

In [ ]:
def avoids(word, forbidden):
    for letter in word.lower():
        if letter in forbidden:
            return False
    return True

Wir können `False` zurückgeben, sobald wir einen verbotenen Buchstaben finden; wenn wir am Ende der Schleife angelangt sind, geben wir `True` zurück.

`uses_only` ist ähnlich, aber die Semantik der Bedingung ist umgekehrt:


In [ ]:
def uses_only(word, available):
    for letter in word.lower(): 
        if letter not in available:
            return False
    return True

Anstatt einer Liste verbotener Buchstaben haben wir eine Liste erlaubter Buchstaben. Wenn wir einen Buchstaben in `word` finden, der nicht in `available` enthalten ist, können wir `False` zurückgeben.

`uses_all` ist ähnlich, außer dass wir die Rolle des Wortes und der Zeichenkette mit den Buchstaben vertauschen:

In [ ]:
def uses_all(word, required):
    for letter in required: 
        if letter not in word.lower():
            return False
    return True

Anstatt die Buchstaben von `word` zu durchlaufen, durchläuft die Schleife die notwendigen Buchstaben. Wenn einer der notwendigen Buchstaben nicht im Wort enthalten ist, können wir `False` zurückgeben.

Wenn Sie schon wie ein Informatiker denken würden, dann würden Sie erkannt haben, dass `uses_all` eine Instanz eines zuvor gelösten Problems ist und Sie hätten geschrieben:

In [ ]:
def uses_all(word, required):
    return uses_only(required, word)

Das ist ein Beispiel für ein Form der Programmentwicklung die sich **Zurückführen auf ein vorher gelöstes Problem** (*reduction to a previously solved problem*) nennt. Das bedeutet, dass wir erkennen, dass das Problem welches wir lösen wollen, eine Instanz eines Problems ist, welches wir schon gelöst haben und wir entsprechend die vorhandene Lösung verwenden.

### 9.4 Schleifen mit Indizes

Die Funktionen in den vorherigen Abschnitten wurden mit `for`-Schleifen implementiert, da nur die Zeichen in den Zeichenketten benötigt wurden, nicht aber deren Indizes.

Für die Funktion `is_abecedarian` müssen wir nebeneinanderliegende Buchstaben miteinander vergleichen, was mit einer `for`-Schleife etwas schwierig ist:


In [ ]:
def is_abecedarian(word):
    previous = word[0]
    for c in word:
        if c < previous:
            return False
        previous = c
    return True

Eine Alternative ist die Verwendung von Rekursion:

In [ ]:
def is_abecedarian(word):
    if len(word) <= 1:
        return True
    if word[0] > word[1]:
        return False
    return is_abecedarian(word[1:])

Eine weitere Option ist eine `while`-Schleife:

In [ ]:
def is_abecedarian(word):
    i = 0
    while i < len(word)-1:
        if word[i+1] < word[i]:
            return False
        i = i+1
    return True

Die Schleife startet mit `i = 0` und endet wenn `i = len(word)-1` gilt. Bei jedem Schleifendurchlauf wird das *i*-te Zeichen (was wir uns als das aktuelle Zeichen vorstellen können) mit dem *i+1*-ten Zeichen (welches wir uns als das nächste Zeichen vorstellen können) verglichen. 

Wenn das nächste Zeichen (alphabetisch) kleiner als das aktuelle Zeichen ist, dann haben wir eine Verletzung der alphabetischen Reihenfolge entdeckt und geben `False` zurück.

Wenn wir das Ende der Schleife erreichen, ohne eine solche Verletzung zu finden, dann hat das Wort unseren Test bestanden. Überlegen Sie sich den Ablauf für das Wort "Beginn", um sich von der Richtigkeit der Schleife zu überzeugen. Die Länge des Wortes ist 6, so dass `i` beim letzten Schleifendurchlauf den Wert 4 hat, was der Index des vorletzten Zeichens ist. In der letzten Iteration wird das vorletzte mit dem letzten Zeichen verglichen - was genau das ist, was wir brauchen.

Hier ist eine Variante von `is_palindrome` (siehe [Abschnitt 6](seminar06.ipynb#Aufgabe-3), die zwei Indizes verwendet. Einer startet am Anfang und wird nach oben gezählt, der andere startet am Ende und wird nach unten gezählt.

In [ ]:
def is_palindrome(word):
    i = 0
    j = len(word)-1

    while i<j:
        if word[i] != word[j]:
            return False
        i = i+1
        j = j-1

    return True

Wir könnten das ganze auch auf ein bereits zuvor gelöstes Problem zurückführen und stattdessen schreiben:

In [ ]:
def is_palindrome(word):
    return is_reverse(word, word)

is_palindrome("anna")

... indem wir `is_reverse` aus [Abschnitt 8.11](seminar08.ipynb#8.11-Debugging) verwenden:

In [ ]:
def is_reverse(word1, word2):
    '''Um die kürzere Funktion is_palindrom() aufzurufen eingefügt.'''
    if len(word1) != len(word2):
        return False
    
    i = 0
    j = len(word2)-1

    while j > 0:
        if word1[i] != word2[j]:
            return False
        i = i+1
        j = j-1

    return True

### 9.5 Debugging

Programme zu testen ist schwierig. Die Funktionen in diesem Abschnitt sind vergleichsweise einfach zu testen, denn wir können die Ergebnisse von Hand überprüfen. Dennoch ist es schwierig bis unmöglich eine Menge von Wörtern zu wählen, mit denen sich alle möglichen Fehler abdecken lassen.

Schauen wir uns `has_no_e` als Beispiel an, gibt es zwei offensichtliche Fälle, die wir testen müssen: für Wörter, die ein "e" enthalten sollte die Funktion `False` zurückgeben und für Wörter, die kein "e" enthalten sollte sie "True" zurückgeben. Für beide Fälle fällt es uns leicht, ein Testwort zu finden.

Bei jedem der Fälle gibt es jedoch einige nicht so offensichtliche Teilfälle. Unter den Wörtern die ein "e" enthalten, sollten wir Wörter testen, die ein "e" am Anfang, am Ende und irgendwo in der Mitte enthalten. Wir sollten lange Wörter, kurze Wörter und sehr kurze Wörter, wie zum Beispiel die leere Zeichenkette, testen. Die leere Zeichenkette ist ein Beispiel für einen **Spezialfall** - einer der nicht offensichtlichen Fälle, bei dem sich oft Fehler verstecken.

Zusätzlich zu den Testfällen, die wir selber erzeugen, können wir unser Programm auch mit einer Wortliste wie z.B. `top10000de.txt` testen. Indem wir uns die Ausgabe anschauen, finden wir vielleicht Fehler. Aber wir sollten vorsichtig sein: es kann sein, dass wir eine Art von Fehlern finden (Wörter, die nicht enthalten sein sollten, es aber trotzdem sind) aber nicht die andere (Wörter die enthalten sein sollten, es aber nicht sind).

Im Allgemeinen kann Testen uns helfen, Fehler zu finden, aber es ist nicht einfach, eine gute Menge von Testfällen zu erzeugen. Und selbst wenn wir das machen, können wir uns nie sicher sein, dass unser Programm korrekt ist. Oder, um es mit den Worten eines legendären Informatikers zu sagen:

> Program testing can be used to show the presence of bugs, but 
> never to show their absence!
> 
> — Edsger W. Dijkstra 

(Testen kann uns zwar helfen, Bugs zu finden, jedoch nicht, ihre Abwesenheit zu beweisen.)

### 9.6 Glossar
Legen wir uns eine Liste mit den wichtigsten Begriffen an, die wir im Kapitel 9 gelernt haben:

- Dateiobjekt:
- Zurückführen auf ein vorher gelöstes Problem:
- Spezialfall: ein nicht offensichtlicher Fall, in dem sich oft Fehler verstecken.

Ergänzen Sie die Liste in eigenen Worten. Das ist eine gute Erinnerungs- und Übungsmöglichkeit.

### 9.7 Übung



### Aufgabe 7

Hier ist ein weiteres [Car Talk Rätsel](http://www.cartalk.com/content/puzzlers):

> Als ich letztens auf der Autobahn gefahren bin ist mir auf meinem Kilometerzähler etwas aufgefallen. Wie die meisten Kilometerzähler hat er sechs Stellen für die ganzen Kilometer. Wenn also mein Auto 300000 Kilometer gefahren wäre, dann würde ich 3-0-0-0-0-0 sehen. Was ich sah, war sehr interessant. Mir ist aufgefallen, dass die letzten vier Ziffern ein Palindrom gebildet haben, d.h. rückwärts gelesen ergeben sie die gleiche Zahlenfolge wie vorwärts. Beispielswiese ist 5-4-4-5 ein Palindrom. Mein Kilometerzähler könnte also beispielsweise 3-1-5-4-4-5 angezeigt haben. 
>
> Einen Kilometer später ergaben die letzten 5 Ziffern ein Palindrom. Mein Kilometerzähler könnte also beispielsweise 3-6-5-4-5-6 anzeigen. Nach einem weiteren Kilometer ergaben die mittleren 4 der 6 Ziffern ein Palindrom. Bis du bereit? Noch einen Kilometer weiter ergaben alle 6 Ziffern ein Palindrom!
>
> Die Frage ist: was zeigte der Kilometerzähler an, als ich das erste mal darauf schaute?

Schreiben Sie ein Python-Programm, welches alle Zahlen mit sechs Ziffern durchtestet und alle Nummern mit dieser Eigenschaft ausgibt.

In [ ]:
# Implementieren Sie hier das Programm



![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)


1. Es sollte schnell klar werden, dass wir mehrere Funktionen brauchen, die ineinander greifen. Insgesamt werden 3 Funktionen benötigt. Überlegen Sie welche Funktionen benötigt werden und schreiben Sie eventuell schoneinmal die Funktionskopf. 
2. Wir brauchen auf jedenfall eine Funktion, die testet ob eine Zahl ein Palindrom ist. Verwandeln Sie die eingegebene Zahl in einen `string` dann können Sie die einzeilige version von is_palindrom aus [Abschnitt 8.13](seminar08.ipynb#8.13-Übung) wiederverwenden.
3. Testen Sie diese Funktion. Behalten Sie auf jeden Fall im Kopf, dass die Funktion im Lauf der Entwicklung unter Umständen angepasst werden muss. 
4. Sobald `palindrom` funktioniert, schreiben wir eine Funktion, die für einzelne Zahlen prüft, ob die Bedingungen des Rätsels erfüllt sind. Diese Funktion ist schwierig zu testen, da Sie quasi im Kopf durchrechnen müssten, was das Ergebnis ist. Kontrollieren Sie ob Sie die Angaben des Rätsels richtig übernommen haben und geben Sie der Funktion ggf. einen Vertrauensvorschuss.
5. Die Funktion ruft `palindrom` mit verschiedenen Werten auf, die aus der Zahl errechnet werden, die eingegeben wird. Beim erneuten Lesen der Aufgabenstellung sollte auffallen, dass wir die eingegebene Zahl auf verschiedene Längen kürzen müssen.
6.  Am besten funktiert das, wenn Sie Start- und Endwerte mit übergeben und diese dann auch an palindrom weitergeben. Hier müssen wir `palindrom` anpassen, indem wir mehr Werte übergeben und den `string` mit dem Klammernoperator entsprechend kürzen. 
7. Insgesamt müssen 4 Zahlen überprüft werden, dabei kann abgebrochen werden, sobald einer der Tests `False` zurückgibt. Zuerst wird palindrom mit i, 2 und 6 aufgerufen, dann mit i+1, 1 und 6. Schreiben Sie die anderen beiden Tests selber und ergänzen Sie wie notwendig die `return`-Anweißungen. *Hinweiß: Sie können die Funktion mit 199999 und 111111 testen, ersteres gibt `True` letzteres `False` zurück.*  
8. Wenn diese Tests das gewüschte Ergebnis liefern, nehmen Sie an, dass die Funktion richtig funktioniert und schreiben Sie die letzte Funktion die wir benötigen. Sie iteriert durch alle möglichen Zählerstände und gibt alle aus, die die Bedingung des Rätsels erfüllen. Überlegen Sie was der kleinstmögliche Zählerstand ist. Überlegen Sie auch was der größtmögliche Zählerstand ist.
9. Erstellen Sie eine Variable mit dem kleinstmöglichen Zählerstand und eine Schleife, deren Abbruchbedingung der größtmögliche Zählerstand ist.
10. In dieser Schleife prüfen Sie den momentanen Wert des Zählers in `check()` und wenn die Funktion `True` zurückliefert, drucken sie den Wert des Zählers aus. Wenn Sie eine `while`-Schleife verwenden, vergessen Sie nicht den Wert des Zählers zu inkrementieren. 

*Hinweiß: 198888 und 199999 sollten als Lösungen rauskommen*

Eine weitere Lösung finden Sie [hier](http://thinkpython2.com/code/cartalk2.py).

In [ ]:
def palindrom(i, start, end):
    s=str(i)[start:end]
    return s[::-1]==s
    

    
def check(i):
    if palindrom(i, 2,6):
        if palindrom(i+1, 1, 6):
            if palindrom(i+2,1,5):
                if palindrom(i+3,0,6):
                    return True
    return False            





def check_all():
    i = 100000
    print("Hier die Zählerstände die Lösungen sind: \n")
    while i <= 999999:
        if check(i):
            print(i)
        i = i + 1

        
check_all()

### Aufgabe 8

Und noch ein [Car Talk Rätsel](http://www.cartalk.com/content/puzzlers) welches sich mit Suche lösen lässt:

> Letztens hat mich meine Mutter besucht und uns ist aufgefallen, dass die zwei Ziffern, die mein Alter angegeben rückwärts gelesen ihrem Alter entsprachen. Wir haben uns gefragt, wie oft das über die Jahre schon passiert ist, aber wir wurden abgelenkt und haben keine Antwort gefunden.
> Als ich nach Hause kam ist mir aufgefallen, dass die Ziffern unserer Alter sich bisher sechs mal umkehren ließen. Mir fiel auch auf, dass es in ein paar Jahren nochmal passieren würde, wenn es uns bis dahin gut geht. Und wenn wir richtig viel Glück haben, würde es danach noch einmal passieren. Anders gesagt: es könnte acht mal insgesamt passieren. Die Frage ist also, wie alt ich gerade bin?

Schreiben Sie ein Programm, welches nach einer Lösung für dieses Rätsel sucht. Hinweis: Sie könnten die Zeichenketten-Methode [zfill](http://python-reference.readthedocs.io/en/latest/docs/str/zfill.html) nützlich finden. Lösung: http://thinkpython2.com/code/cartalk3.py

In [ ]:
# Implementieren Sie hier ihr Programm




![Spoiler Alert](https://imgs.xkcd.com/comics/spoiler_alert.png)
([Spoiler Alert](https://xkcd.com/109/), Randall Munroe)

1. Auch dies ist wieder ein Problem für das wir mehrere Funktionen schreiben müssen. Überlegen Sie  zunächst in welche Bestandteile sie das Problem aufteilen können.
2. Wir brauchen insgesammt 4 Funktionen, diese sind stärker miteinander verbunden als in der vorherigen Aufgabe, wir versuchen dennoch Sie nach und nach zu schreiben.
3. Wir schreiben zunächst eine Funktion, die testet ob sich das Alter herumdrehen lässt. Sie brauchen 2 Strings der gleichen Länge, dafür können Sie `zfill(2)` verwenden. Orientieren Sie sich an `palindrom` aus der vorherigen Aufgabe.
4. Die Funktion `are_reversed()` wird in 2 weiteren Funktionen dieser Aufgabe verwenden, die sich einigen Code teilen. Schreiben Sie also zunächst eine der Funktionen, duplizieren Sie sie dann und passen Sie sie entsprechen an.
5. In der ersten Funktion wird gezählt, wie oft sich für einen gegebenen Altersunterschied das Alter der Mutter und der Tochter umdrehen lässt. 
6. Erstellen Sie eine Variable die das Alter der Tochter simuliert. Initialisieren Sie diese mit 0. Erstellen Sie eine Variable die zählt wie oft sich das Alter umdrehen lässt.
7. Da Sie jedes mögliche Alter für den gegebenen Abstand testen wollen erstellen Sie ein Schleife. Da Sie das Alter der Mutter als Abbruchbedingung nehmen wollen und wir die entsprechende Variable erst in der Schleife initialisieren verwenden Sie eine Schleife die erst abbricht, wenn in der Schleife eine Bedingung erfüllt wird. (*`While True`*)
8. Das Alter der Mutter ergibt sich aus dem Alter der Tochter und der Differenz. Erstellen Sie die Variable entsprechend. 
9. Rufen Sie `are_reversed()` mit mother und daughter auf. Wird `True` zurückgegeben, muss count inkrementiert werden.
10. Testen Sie das Alter der Mutter. Ist es größer als 100 brechen Sie die Schleife mit einer `break`-Anweißung ab.
11. Vergessen Sie nicht vor Abschluss des Schleifendurchlaufs die Variable `daughter` zu inkrementieren.
12. Nach Verlassen der Schleife geben Sie mit der `return`-Anweißung den Zähler zurück. 
13. Kopieren Sie die Funktion und geben Sie ihr einen neuen Namen. Weitere Änderungen der Funktion führen wir an gegebener Stelle durch. 
14. Schreiben Sie nun zunächst eine allgemeine Funktion. Diese wird nach und nach den Altersabstand zwischen Mutter und Tocher erhöhen und prüfen ob die Bedingung des Rätsels erfüllt ist. Da wir den Altersabstand an die anderen Funktionen weiterreichen, erstellen Sie hier die benötigte Variable. Legen Sie einen sinnvollen Mindestabstand fest. 
15. Schreiben Sie eine Schleife die den Altersabstand graduell vergrößert. Wählen Sie einen sinnvollen Maximalabstand als Abbruchbedingung.
16. In der Schleife wird `num_instances()`aufgerufen und der Rückgabewert einer Variablen zugewießen. Diese Variable wird dann geprüft um zu schauen ob dieser Altersabstand die Bedingung des Rätsels erfüllt. Was ist diese Bedinung?
17. Ist die Bedinung erfüllt wird `list_instance` mit dieser Differenz aufgerufen. Diese Funktion prüft das Alter analog zu `num_instances()` und gibt das Alter aus, das die Lösung des Rätsels dastellt. Wir brauchen hierbei `print`-Anweißungen, eine für den Kopf der Tablle und eine die das Alter ausdruckt, wenn sich das Alter von Mutter und Tochter genau x mal bisher umdrehen ließ. 

*Hinweiß: Vergessen Sie nicht, diff in der Schleife zu inkrementieren!*





In [ ]:
def are_reversed(i,j):
    i= str(i).zfill(2)
    j= str(j).zfill(2)
    if i==j[::-1]:
        return True
    

def num_instances(diff):
    daughter = 0
    count = 0
    while True:
        mother = daughter + diff
        if are_reversed(daughter, mother):
            count = count + 1
        if mother > 100:
            break
        daughter = daughter + 1
    return count


def list_instance(diff):
    daughter=0
    count=0
    print("daughter mother")
    while True:
        mother= daughter+diff
        if are_reversed(daughter, mother):
            count=count+1
            if count==6:
                print(daughter,"     ",mother)
        if mother > 100:
            return
        daughter=daughter+1


def check_ages():
    diff = 13
    while diff < 70:
        n = num_instances(diff)
        if n == 8:
            list_instance(diff)
        diff = diff + 1 

check_ages()


![Speichern](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/floppy.png) Speichern Sie dieses Notebook, so dass Ihre Änderungen nicht verlorengehen (nicht auf einem Pool-Rechner). Klicken Sie dazu oben links auf das Disketten-Icon und nutzen Sie beispielsweise einen USB-Stick, E-Mail, Google Drive, Dropbox oder Ihre [HU-Box](https://box.hu-berlin.de/).  

![Smiley](https://upload.wikimedia.org/wikipedia/commons/thumb/7/79/Face-smile.svg/48px-Face-smile.svg.png)

Herzlichen Glückwunsch! Sie haben das 9. Kapitel geschafft. Weiter geht es in [10: Listen](seminar10.ipynb).